In [1]:
from gurobipy import *

In [2]:
m = Model("clique")

Using license file /Users/melkebir/gurobi.lic
Academic license - for non-commercial use only


In [3]:
x1 = m.addVar(vtype=GRB.BINARY, name="v_1")
x2 = m.addVar(vtype=GRB.BINARY, name="v_2")
x3 = m.addVar(vtype=GRB.BINARY, name="v_3")
x4 = m.addVar(vtype=GRB.BINARY, name="v_4")
x5 = m.addVar(vtype=GRB.BINARY, name="v_5")

In [5]:
m.addConstr(x1+x4 <= 1)
m.addConstr(x2+x3 <= 1)
m.addConstr(x2+x5 <= 1)
m.addConstr(x4+x5 <= 1)

<gurobi.Constr *Awaiting Model Update*>

In [6]:
m.setObjective(x1 + x2 + x3 + x4 + x5, GRB.MAXIMIZE)

In [7]:
m.optimize()

Gurobi Optimizer version 9.0.1 build v9.0.1rc0 (mac64)
Optimize a model with 5 rows, 5 columns and 10 nonzeros
Model fingerprint: 0xfc539a27
Variable types: 0 continuous, 5 integer (5 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Found heuristic solution: objective 2.0000000
Presolve removed 5 rows and 5 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.03 seconds
Thread count was 1 (of 4 available processors)

Solution count 2: 3 

Optimal solution found (tolerance 1.00e-04)
Best objective 3.000000000000e+00, best bound 3.000000000000e+00, gap 0.0000%


In [8]:
for v in m.getVars():
    print(v.varName, v.x)

v_1 1.0
v_2 0.0
v_3 1.0
v_4 0.0
v_5 1.0


In [9]:
def parse_DIMACS(filename, relax):
    edges = set()
    with open(filename) as f:
        for line in f:
            if line.startswith('p'):
                nrVertices = int(line.rstrip("\n").split()[-2])
            elif line.startswith('e'):
                u = int(line.rstrip("\n").split()[-2])-1
                v = int(line.rstrip("\n").split()[-1])-1
                edges |= set([(u,v)])
    m = Model(filename)
    t = GRB.CONTINUOUS if relax else GRB.BINARY
    x = m.addVars(range(nrVertices), vtype=t)
    m.update()
    for i in range(nrVertices):
        for j in range(i+1, nrVertices):
            if ((i,j) not in edges) and ((j,i) not in edges):
                m.addConstr(x[i] + x[j] <= 1)
    if relax:
        for i in range(nrVertices):
            m.addConstr(0<=x[i]<=1)
    m.update()
    m.setObjective(quicksum(x[i] for i in range(nrVertices)), GRB.MAXIMIZE)
    m.update()
    return m, nrVertices

In [10]:
m, nrVertices = parse_DIMACS("./C125.9.clq.txt", False)

In [11]:
m.optimize()

Gurobi Optimizer version 9.0.1 build v9.0.1rc0 (mac64)
Optimize a model with 787 rows, 125 columns and 1574 nonzeros
Model fingerprint: 0x217f6bdd
Variable types: 0 continuous, 125 integer (125 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Found heuristic solution: objective 26.0000000
Presolve removed 312 rows and 0 columns
Presolve time: 0.01s
Presolved: 475 rows, 125 columns, 1217 nonzeros
Variable types: 0 continuous, 125 integer (125 binary)

Root relaxation: objective 4.322903e+01, 353 iterations, 0.02 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0   43.22903    0  124   26.00000   43.22903  66.3%     -    0s
H    0     0                      31.0000000   43.22903  39.4%     -    0s
     0     0   42.39415    0  125   31.00000   42.3941

In [12]:
for v in m.getVars():
    if v.x > 0.5:
        print(v.varName, v.x)

C0 1.0
C1 1.0
C6 1.0
C10 1.0
C17 1.0
C18 1.0
C24 1.0
C28 1.0
C30 1.0
C33 1.0
C43 1.0
C44 1.0
C46 1.0
C47 1.0
C48 1.0
C53 1.0
C67 1.0
C69 1.0
C70 1.0
C73 1.0
C76 1.0
C78 1.0
C79 1.0
C84 1.0
C97 1.0
C100 1.0
C109 1.0
C113 1.0
C114 1.0
C115 1.0
C116 1.0
C120 1.0
C121 1.0
C124 1.0
